In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import json
import os 
import kaggle
import torch
from torch.utils.data import Dataset, DataLoader
import torch.optim as optim
import torch.nn as nn
from torch.utils.data import Dataset, DataLoader, Subset
from PIL import Image
from sklearn.model_selection import train_test_split
import torchvision.models as models 

In [2]:
with open("kaggle.json") as f:
    kaggle_crediential = json.load(f)

In [3]:
os.environ['KAGGLE_USERNAME'] = kaggle_crediential['username']
os.environ['KAGGLE_KEY'] = kaggle_crediential['key']

In [4]:
with open("D:\instances_train2017.json\instances_train2017.json") as f:
    data = json.load(f)

In [5]:
print(data.keys())

dict_keys(['info', 'licenses', 'images', 'annotations', 'categories'])


In [6]:
data.get('info')

{'description': 'COCO 2017 Dataset',
 'url': 'http://cocodataset.org',
 'version': '1.0',
 'year': 2017,
 'contributor': 'COCO Consortium',
 'date_created': '2017/09/01'}

In [7]:
data.get('licenses')

[{'url': 'http://creativecommons.org/licenses/by-nc-sa/2.0/',
  'id': 1,
  'name': 'Attribution-NonCommercial-ShareAlike License'},
 {'url': 'http://creativecommons.org/licenses/by-nc/2.0/',
  'id': 2,
  'name': 'Attribution-NonCommercial License'},
 {'url': 'http://creativecommons.org/licenses/by-nc-nd/2.0/',
  'id': 3,
  'name': 'Attribution-NonCommercial-NoDerivs License'},
 {'url': 'http://creativecommons.org/licenses/by/2.0/',
  'id': 4,
  'name': 'Attribution License'},
 {'url': 'http://creativecommons.org/licenses/by-sa/2.0/',
  'id': 5,
  'name': 'Attribution-ShareAlike License'},
 {'url': 'http://creativecommons.org/licenses/by-nd/2.0/',
  'id': 6,
  'name': 'Attribution-NoDerivs License'},
 {'url': 'http://flickr.com/commons/usage/',
  'id': 7,
  'name': 'No known copyright restrictions'},
 {'url': 'http://www.usa.gov/copyright.shtml',
  'id': 8,
  'name': 'United States Government Work'}]

In [8]:
data.get('images')

[{'license': 3,
  'file_name': '000000391895.jpg',
  'coco_url': 'http://images.cocodataset.org/train2017/000000391895.jpg',
  'height': 360,
  'width': 640,
  'date_captured': '2013-11-14 11:18:45',
  'flickr_url': 'http://farm9.staticflickr.com/8186/8119368305_4e622c8349_z.jpg',
  'id': 391895},
 {'license': 4,
  'file_name': '000000522418.jpg',
  'coco_url': 'http://images.cocodataset.org/train2017/000000522418.jpg',
  'height': 480,
  'width': 640,
  'date_captured': '2013-11-14 11:38:44',
  'flickr_url': 'http://farm1.staticflickr.com/1/127244861_ab0c0381e7_z.jpg',
  'id': 522418},
 {'license': 3,
  'file_name': '000000184613.jpg',
  'coco_url': 'http://images.cocodataset.org/train2017/000000184613.jpg',
  'height': 336,
  'width': 500,
  'date_captured': '2013-11-14 12:36:29',
  'flickr_url': 'http://farm3.staticflickr.com/2169/2118578392_1193aa04a0_z.jpg',
  'id': 184613},
 {'license': 3,
  'file_name': '000000318219.jpg',
  'coco_url': 'http://images.cocodataset.org/train2017/0

In [9]:
data.get('annotations')

[{'segmentation': [[239.97,
    260.24,
    222.04,
    270.49,
    199.84,
    253.41,
    213.5,
    227.79,
    259.62,
    200.46,
    274.13,
    202.17,
    277.55,
    210.71,
    249.37,
    253.41,
    237.41,
    264.51,
    242.54,
    261.95,
    228.87,
    271.34]],
  'area': 2765.1486500000005,
  'iscrowd': 0,
  'image_id': 558840,
  'bbox': [199.84, 200.46, 77.71, 70.88],
  'category_id': 58,
  'id': 156},
 {'segmentation': [[247.71,
    354.7,
    253.49,
    346.99,
    276.63,
    337.35,
    312.29,
    333.49,
    364.34,
    331.57,
    354.7,
    327.71,
    369.16,
    325.78,
    376.87,
    333.49,
    383.61,
    330.6,
    379.76,
    321.93,
    365.3,
    320.0,
    356.63,
    317.11,
    266.02,
    331.57,
    260.24,
    334.46,
    260.24,
    337.35,
    242.89,
    338.31,
    234.22,
    338.31,
    234.22,
    348.92,
    239.04,
    353.73,
    248.67,
    355.66,
    252.53,
    353.73]],
  'area': 1545.4213000000007,
  'iscrowd': 0,
  'image_id

In [10]:
data.get('categories')

[{'supercategory': 'person', 'id': 1, 'name': 'person'},
 {'supercategory': 'vehicle', 'id': 2, 'name': 'bicycle'},
 {'supercategory': 'vehicle', 'id': 3, 'name': 'car'},
 {'supercategory': 'vehicle', 'id': 4, 'name': 'motorcycle'},
 {'supercategory': 'vehicle', 'id': 5, 'name': 'airplane'},
 {'supercategory': 'vehicle', 'id': 6, 'name': 'bus'},
 {'supercategory': 'vehicle', 'id': 7, 'name': 'train'},
 {'supercategory': 'vehicle', 'id': 8, 'name': 'truck'},
 {'supercategory': 'vehicle', 'id': 9, 'name': 'boat'},
 {'supercategory': 'outdoor', 'id': 10, 'name': 'traffic light'},
 {'supercategory': 'outdoor', 'id': 11, 'name': 'fire hydrant'},
 {'supercategory': 'outdoor', 'id': 13, 'name': 'stop sign'},
 {'supercategory': 'outdoor', 'id': 14, 'name': 'parking meter'},
 {'supercategory': 'outdoor', 'id': 15, 'name': 'bench'},
 {'supercategory': 'animal', 'id': 16, 'name': 'bird'},
 {'supercategory': 'animal', 'id': 17, 'name': 'cat'},
 {'supercategory': 'animal', 'id': 18, 'name': 'dog'},

In [11]:
data["images"][2]

{'license': 3,
 'file_name': '000000184613.jpg',
 'coco_url': 'http://images.cocodataset.org/train2017/000000184613.jpg',
 'height': 336,
 'width': 500,
 'date_captured': '2013-11-14 12:36:29',
 'flickr_url': 'http://farm3.staticflickr.com/2169/2118578392_1193aa04a0_z.jpg',
 'id': 184613}

In [12]:
data["categories"][16]

{'supercategory': 'animal', 'id': 18, 'name': 'dog'}

In [13]:
data['annotations']

[{'segmentation': [[239.97,
    260.24,
    222.04,
    270.49,
    199.84,
    253.41,
    213.5,
    227.79,
    259.62,
    200.46,
    274.13,
    202.17,
    277.55,
    210.71,
    249.37,
    253.41,
    237.41,
    264.51,
    242.54,
    261.95,
    228.87,
    271.34]],
  'area': 2765.1486500000005,
  'iscrowd': 0,
  'image_id': 558840,
  'bbox': [199.84, 200.46, 77.71, 70.88],
  'category_id': 58,
  'id': 156},
 {'segmentation': [[247.71,
    354.7,
    253.49,
    346.99,
    276.63,
    337.35,
    312.29,
    333.49,
    364.34,
    331.57,
    354.7,
    327.71,
    369.16,
    325.78,
    376.87,
    333.49,
    383.61,
    330.6,
    379.76,
    321.93,
    365.3,
    320.0,
    356.63,
    317.11,
    266.02,
    331.57,
    260.24,
    334.46,
    260.24,
    337.35,
    242.89,
    338.31,
    234.22,
    338.31,
    234.22,
    348.92,
    239.04,
    353.73,
    248.67,
    355.66,
    252.53,
    353.73]],
  'area': 1545.4213000000007,
  'iscrowd': 0,
  'image_id

In [14]:
data['annotations'][1000]['category_id']

44

In [15]:
cats = set()

for el in range(len(data['annotations'])):
    cats.add(data['annotations'][el]['category_id'])


In [16]:
cats

{1,
 2,
 3,
 4,
 5,
 6,
 7,
 8,
 9,
 10,
 11,
 13,
 14,
 15,
 16,
 17,
 18,
 19,
 20,
 21,
 22,
 23,
 24,
 25,
 27,
 28,
 31,
 32,
 33,
 34,
 35,
 36,
 37,
 38,
 39,
 40,
 41,
 42,
 43,
 44,
 46,
 47,
 48,
 49,
 50,
 51,
 52,
 53,
 54,
 55,
 56,
 57,
 58,
 59,
 60,
 61,
 62,
 63,
 64,
 65,
 67,
 70,
 72,
 73,
 74,
 75,
 76,
 77,
 78,
 79,
 80,
 81,
 82,
 84,
 85,
 86,
 87,
 88,
 89,
 90}

In [17]:
len(cats)

80

#### There are total 80 categories

In [18]:
len(data['annotations'])

860001

In [19]:
folder = r"D:/Dataset/coco2017/train2017"
count = len([name for name in os.listdir(folder) if name.lower().endswith(('.jpg'))])

print("Number of images:", count)

Number of images: 118287


### As you can see we have less number of images and more number of categories means this is a problem of multi-class binary entropy

In [20]:
data['annotations'][5]

{'segmentation': [[374.46,
   310.42,
   386.68,
   310.17,
   394.32,
   308.64,
   398.4,
   303.54,
   397.38,
   301.0,
   401.71,
   301.51,
   403.49,
   296.16,
   402.98,
   291.32,
   402.22,
   286.48,
   400.95,
   283.42,
   394.32,
   281.13,
   391.78,
   277.06,
   388.98,
   272.47,
   387.7,
   270.94,
   382.1,
   270.18,
   378.53,
   267.89,
   374.46,
   263.81,
   368.35,
   260.76,
   366.05,
   256.94,
   363.25,
   253.88,
   358.67,
   251.08,
   357.14,
   247.51,
   353.83,
   245.22,
   351.03,
   244.46,
   345.93,
   244.97,
   342.88,
   248.02,
   341.35,
   251.08,
   339.57,
   253.63,
   337.02,
   255.15,
   338.8,
   259.23,
   339.41,
   266.1,
   346.51,
   265.74,
   349.35,
   269.3,
   342.25,
   272.49,
   339.41,
   275.69,
   343.67,
   277.11,
   348.29,
   274.27,
   353.61,
   276.4,
   357.17,
   283.86,
   357.88,
   292.38,
   355.75,
   301.62,
   352.9,
   306.95,
   350.42,
   306.95,
   347.93,
   306.95,
   351.48,
   311.21,
   

In [21]:
num_images = count
num_classes = len(cats)

# Sort data['images'] by filename to match your folder's sorted order
data['images'] = sorted(data['images'], key=lambda x: x['file_name'])

# Now build your mappings with the sorted order
img_id_to_idx = {img['id']: i for i, img in enumerate(data['images'])}


# Sort categories by their ID to ensure consistent ordering
data['categories'] = sorted(data['categories'], key=lambda x: x['id'])

# Now create the mapping
cat_id_to_idx = {cat['id']: i for i, cat in enumerate(data['categories'])}


y = np.zeros((num_images, num_classes), dtype=int)
for ann in data['annotations']:
    img_idx = img_id_to_idx[ann['image_id']]
    cat_idx = cat_id_to_idx[ann['category_id']]
    y[img_idx][cat_idx] = 1


In [22]:
y[1]

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0])

In [23]:
data['categories']

[{'supercategory': 'person', 'id': 1, 'name': 'person'},
 {'supercategory': 'vehicle', 'id': 2, 'name': 'bicycle'},
 {'supercategory': 'vehicle', 'id': 3, 'name': 'car'},
 {'supercategory': 'vehicle', 'id': 4, 'name': 'motorcycle'},
 {'supercategory': 'vehicle', 'id': 5, 'name': 'airplane'},
 {'supercategory': 'vehicle', 'id': 6, 'name': 'bus'},
 {'supercategory': 'vehicle', 'id': 7, 'name': 'train'},
 {'supercategory': 'vehicle', 'id': 8, 'name': 'truck'},
 {'supercategory': 'vehicle', 'id': 9, 'name': 'boat'},
 {'supercategory': 'outdoor', 'id': 10, 'name': 'traffic light'},
 {'supercategory': 'outdoor', 'id': 11, 'name': 'fire hydrant'},
 {'supercategory': 'outdoor', 'id': 13, 'name': 'stop sign'},
 {'supercategory': 'outdoor', 'id': 14, 'name': 'parking meter'},
 {'supercategory': 'outdoor', 'id': 15, 'name': 'bench'},
 {'supercategory': 'animal', 'id': 16, 'name': 'bird'},
 {'supercategory': 'animal', 'id': 17, 'name': 'cat'},
 {'supercategory': 'animal', 'id': 18, 'name': 'dog'},

In [24]:
img_id_to_idx.keys()

dict_keys([9, 25, 30, 34, 36, 42, 49, 61, 64, 71, 72, 73, 74, 77, 78, 81, 86, 89, 92, 94, 109, 110, 113, 127, 133, 136, 138, 142, 143, 144, 149, 151, 154, 164, 165, 192, 194, 196, 201, 208, 241, 247, 250, 257, 260, 263, 283, 294, 307, 308, 309, 312, 315, 321, 322, 326, 328, 332, 338, 349, 357, 359, 360, 368, 370, 382, 384, 387, 389, 394, 395, 397, 400, 404, 415, 419, 428, 431, 436, 438, 443, 446, 450, 459, 471, 472, 474, 486, 488, 490, 491, 502, 508, 510, 514, 520, 529, 531, 532, 536, 540, 542, 544, 560, 562, 564, 569, 572, 575, 581, 584, 589, 590, 595, 597, 599, 605, 612, 620, 623, 625, 626, 629, 634, 636, 641, 643, 650, 656, 659, 661, 670, 671, 673, 675, 681, 684, 690, 692, 693, 699, 706, 711, 714, 715, 716, 722, 723, 730, 731, 735, 753, 754, 757, 761, 762, 764, 772, 775, 781, 790, 795, 797, 801, 810, 813, 821, 825, 827, 828, 831, 836, 839, 853, 873, 882, 897, 901, 902, 908, 909, 913, 923, 925, 927, 934, 939, 941, 943, 955, 960, 962, 965, 969, 974, 977, 982, 984, 985, 987, 996, 999, 

In [25]:
y.shape

(118287, 80)

In [26]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

In [27]:
device

device(type='cuda')

In [28]:
from torchvision.transforms import transforms

customTransform = transforms.Compose([
    transforms.Resize(256),
    transforms.CenterCrop(224),
    transforms.ToTensor(),
    transforms.Normalize(mean = [0.485,0.456,0.406],std = [0.229,0.224,0.225])
])

In [29]:
import re

class CustomDataset(Dataset):
    def __init__(self, folder, labels, transform):
        self.folder = folder
        files = [f for f in os.listdir(folder) if f.endswith(('.jpg', '.png'))]
        
        # Sort numerically by the ID in the filename
        self.files = sorted(files, key=lambda x: int(re.findall(r'\d+', x)[0]))
        
        self.labels = list(labels)
        self.transform = transform

    def __len__(self):
        return len(self.files)

    def __getitem__(self, idx):
        img_path = os.path.join(self.folder, self.files[idx])
        img = Image.open(img_path).convert("RGB")
        img = self.transform(img)
        label = torch.tensor(self.labels[idx], dtype=torch.float32)
        return img, label


In [30]:
dataset = CustomDataset(folder, y, customTransform)

In [31]:
num_samples = len(dataset)
indices = np.arange(num_samples)

In [32]:
from sklearn.model_selection import train_test_split
import numpy as np

indices = np.arange(len(dataset))
trainVal_idx, test_idx = train_test_split(indices, test_size=0.15, random_state=42)
train_idx , val_idx = train_test_split(trainVal_idx, test_size=0.15, random_state=42)

# create subsets
train_dataset = Subset(dataset, train_idx)
val_dataset   = Subset(dataset, val_idx)
test_dataset  = Subset(dataset, test_idx)

In [33]:
y = np.array(y)  # your full labels aligned to dataset.files order
y_train = y[train_idx]
y_val   = y[val_idx]
y_test  = y[test_idx]

In [34]:
train_dataset[0]

(tensor([[[2.1290, 2.1290, 2.1290,  ..., 2.1119, 2.1290, 2.1119],
          [2.1462, 2.1462, 2.1462,  ..., 2.1119, 2.1119, 2.1119],
          [2.1290, 2.1290, 2.1290,  ..., 2.1119, 2.1119, 2.1119],
          ...,
          [2.1119, 2.1119, 2.1119,  ..., 2.0948, 2.1119, 2.1119],
          [2.1119, 2.0948, 2.0948,  ..., 2.0948, 2.1119, 2.1119],
          [2.0948, 2.1119, 2.1119,  ..., 2.1119, 2.1119, 2.1119]],
 
         [[2.3060, 2.3060, 2.3060,  ..., 2.2885, 2.3060, 2.2885],
          [2.3235, 2.3235, 2.3235,  ..., 2.2885, 2.2885, 2.2885],
          [2.3060, 2.3060, 2.3060,  ..., 2.2885, 2.2885, 2.2885],
          ...,
          [2.2885, 2.2885, 2.2885,  ..., 2.2710, 2.2885, 2.2885],
          [2.2885, 2.2710, 2.2710,  ..., 2.2710, 2.2885, 2.2885],
          [2.2710, 2.2885, 2.2885,  ..., 2.2885, 2.2885, 2.2885]],
 
         [[2.5529, 2.5529, 2.5529,  ..., 2.5354, 2.5529, 2.5354],
          [2.5703, 2.5703, 2.5703,  ..., 2.5354, 2.5354, 2.5354],
          [2.5529, 2.5529, 2.5529,  ...,

In [35]:
y_train[0]

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0])

In [36]:
test_dataset[0]

(tensor([[[-1.2788, -1.2788, -1.2959,  ..., -1.7583, -1.7240, -1.7240],
          [-1.2788, -1.2788, -1.3130,  ..., -1.7925, -1.7754, -1.7412],
          [-1.2959, -1.2788, -1.3130,  ..., -1.7925, -1.7754, -1.7754],
          ...,
          [-1.9295, -1.9124, -1.8610,  ...,  0.7419,  0.6221, -0.2171],
          [-1.9124, -1.8953, -1.9295,  ...,  0.6392,  0.6221, -0.8849],
          [-1.9124, -1.9467, -1.8953,  ..., -0.7137, -1.1760, -1.7069]],
 
         [[-1.3354, -1.3529, -1.3704,  ..., -1.8256, -1.8081, -1.7906],
          [-1.3354, -1.3354, -1.3529,  ..., -1.8256, -1.8431, -1.8081],
          [-1.3354, -1.3179, -1.3529,  ..., -1.8256, -1.8606, -1.8431],
          ...,
          [-1.8081, -1.8256, -1.8081,  ..., -0.4951, -0.5301, -1.2304],
          [-1.8431, -1.8081, -1.8431,  ..., -0.5476, -0.5301, -1.5805],
          [-1.8256, -1.8431, -1.8431,  ..., -1.4405, -1.7206, -1.8782]],
 
         [[-1.2816, -1.2990, -1.3164,  ..., -1.6302, -1.6302, -1.6302],
          [-1.2990, -1.3164,

In [37]:
y_test[0]

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0,
       0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0])

In [38]:
train_loader = DataLoader(train_dataset, batch_size=32, shuffle=True,
                          num_workers=0, pin_memory=True)
val_loader = DataLoader(val_dataset,batch_size=32,shuffle=False,
                        num_workers=0,pin_memory=True)
test_loader  = DataLoader(test_dataset, batch_size=32, shuffle=False,
                          num_workers=0, pin_memory=True)

In [39]:
vgg16 = models.vgg16(pretrained = True)

f:\Dependencies\Lib\site-packages\torchvision\models\_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
f:\Dependencies\Lib\site-packages\torchvision\models\_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=VGG16_Weights.IMAGENET1K_V1`. You can also use `weights=VGG16_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)


In [40]:
vgg16

VGG(
  (features): Sequential(
    (0): Conv2d(3, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (1): ReLU(inplace=True)
    (2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (3): ReLU(inplace=True)
    (4): MaxPool2d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
    (5): Conv2d(64, 128, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (6): ReLU(inplace=True)
    (7): Conv2d(128, 128, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (8): ReLU(inplace=True)
    (9): MaxPool2d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
    (10): Conv2d(128, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (11): ReLU(inplace=True)
    (12): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (13): ReLU(inplace=True)
    (14): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (15): ReLU(inplace=True)
    (16): MaxPool2d(kernel_size=2, stride=2, padding=0, dilation=1

In [41]:
# Unfreeze all VGG16 parameters so the entire model can learn
for param in vgg16.parameters():
    param.requires_grad = False

In [42]:
in_features = vgg16.classifier[0].in_features

vgg16.classifier = nn.Sequential(
    nn.Linear(in_features, 1024),
    nn.BatchNorm1d(1024),
    nn.ReLU(inplace=True),
    nn.Dropout(0.2),

    nn.Linear(1024, 512),
    nn.BatchNorm1d(512),
    nn.ReLU(inplace=True),
    nn.Dropout(0.3),

    nn.Linear(512, 80)   # 80 classes
)

In [43]:
vgg16 = vgg16.to(device)

In [44]:
learning_rate = 0.00001  
epochs = 20

In [45]:
criterion = nn.BCEWithLogitsLoss()
optimizer = optim.Adam(vgg16.classifier.parameters(),lr = learning_rate,weight_decay=1e-4)

In [46]:
class EarlyStopping:
    def __init__(self, patience=5, min_delta=0.0, save_path="best_model.pth", verbose=True):
        """
        patience: #epochs with no improvement before stopping
        min_delta: minimum change to qualify as improvement
        save_path: file to save best model
        verbose: print messages when improving/stopping
        """
        self.patience = patience
        self.min_delta = min_delta
        self.counter = 0
        self.best_loss = np.inf
        self.early_stop = False
        self.save_path = save_path
        self.verbose = verbose

    def __call__(self, val_loss, model):
        """Returns True when training should stop."""
        
        # First ever epoch
        if self.best_loss == np.inf:
            self.best_loss = val_loss
            torch.save(model.state_dict(), self.save_path)
            if self.verbose:
                print(f"[EarlyStopping] Initial model saved. Val Loss: {val_loss:.6f}")
            return False

        # If improvement
        if val_loss < self.best_loss - self.min_delta:
            self.best_loss = val_loss
            self.counter = 0

            torch.save(model.state_dict(), self.save_path)
            if self.verbose:
                print(f"[EarlyStopping] Improvement detected → Model saved. New Val Loss: {val_loss:.6f}")
            return False

        # No improvement
        else:
            self.counter += 1
            if self.verbose:
                print(f"[EarlyStopping] No improvement ({self.counter}/{self.patience}).")

            if self.counter >= self.patience:
                self.early_stop = True
                if self.verbose:
                    print("[EarlyStopping] Patience reached → STOPPING TRAINING.")
                return True

            return False


In [47]:
early_stopping = EarlyStopping(patience=5, min_delta=0.0, save_path="best_model.pth", verbose=True)

In [48]:
for epoch in range(epochs):
    vgg16.train()
    running_loss = 0.0
    num_batches = 0
    correct = 0
    total = 0

    for batch_features, batch_labels in train_loader:
        batch_features = batch_features.to(device, non_blocking=True)
        batch_labels = batch_labels.to(device, non_blocking=True).float()  

        outputs = vgg16(batch_features)           # logits
        loss = criterion(outputs, batch_labels)

        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        running_loss += loss.item()
        num_batches += 1

        # metrics: sigmoid -> threshold
        probs = torch.sigmoid(outputs)            # convert logits → probabilities
        preds = (probs > 0.5).float()

        correct += (preds == batch_labels).sum().item()
        total += batch_labels.numel()

    avg_loss = running_loss / max(1, num_batches)
    accuracy = 100.0 * correct / max(1, total)
    print(f"Epoch [{epoch+1}/{epochs}], Loss: {avg_loss:.4f}, Per-element Accuracy: {accuracy:.2f}%")

    # Validation 
    vgg16.eval()
    val_loss = 0.0
    val_batches = 0
    val_correct = 0
    val_total = 0

    with torch.no_grad():
        for data, targets in val_loader:
            data = data.to(device, non_blocking=True)
            targets = targets.to(device, non_blocking=True).float()

            output = vgg16(data)   # logits
            lossV = criterion(output, targets)
            val_loss += lossV.item()
            val_batches += 1

            # validation metrics using sigmoid
            val_probs = torch.sigmoid(output)
            val_preds = (val_probs > 0.5).float()
            val_correct += (val_preds == targets).sum().item()
            val_total += targets.numel()

    val_loss = val_loss / max(1, val_batches)
    val_accuracy = 100.0 * val_correct / max(1, val_total)
    print(f"Epoch {epoch+1}, Validation Loss: {val_loss:.4f}, Val Per-element Acc: {val_accuracy:.2f}%")

    # Early stopping 
    # call the INSTANCE (not the class) and pass model so best weights are saved
    if early_stopping(val_loss, vgg16):
        print(f"Early stopping triggered at epoch {epoch+1}")
        break

# optionally: load best model weights after training
if early_stopping.save_path is not None:
    vgg16.load_state_dict(torch.load(early_stopping.save_path, map_location=device))
    vgg16.eval()
    print("Best model loaded from", early_stopping.save_path)


Epoch [1/20], Loss: 0.2482, Per-element Accuracy: 93.80%
Epoch 1, Validation Loss: 0.1174, Val Per-element Acc: 97.25%
[EarlyStopping] Initial model saved. Val Loss: 0.117436
Epoch [2/20], Loss: 0.0935, Per-element Accuracy: 97.22%
Epoch 2, Validation Loss: 0.0829, Val Per-element Acc: 97.53%
[EarlyStopping] Improvement detected → Model saved. New Val Loss: 0.082940
Epoch [3/20], Loss: 0.0762, Per-element Accuracy: 97.48%
Epoch 3, Validation Loss: 0.0729, Val Per-element Acc: 97.68%
[EarlyStopping] Improvement detected → Model saved. New Val Loss: 0.072945
Epoch [4/20], Loss: 0.0679, Per-element Accuracy: 97.68%
Epoch 4, Validation Loss: 0.0699, Val Per-element Acc: 97.75%
[EarlyStopping] Improvement detected → Model saved. New Val Loss: 0.069877
Epoch [5/20], Loss: 0.0621, Per-element Accuracy: 97.84%
Epoch 5, Validation Loss: 0.0681, Val Per-element Acc: 97.77%
[EarlyStopping] Improvement detected → Model saved. New Val Loss: 0.068051
Epoch [6/20], Loss: 0.0572, Per-element Accuracy: